In [2]:
import requests
import math
import json
import numpy as np
from random import randint
import requests
import json
from time import sleep


import pandas as pd
import geopandas as gpd

from shapely.geometry import Polygon


import os
os.getcwd()
import geopandas as gp
os.chdir('C:\\Users\\User\conda-exp\Hessen')


In [3]:
#create a geodata frame for the town/cities (Gemeinde)
state=gp.read_file('state.geojson',encoding='utf8')#load geodata for the state
x=[]
for index, row in state.iterrows():
    x.append(row['geometry'].geom_type)
state['geomtype']=x    
state = state.drop(state[state.geomtype=='Point'].index)
IDS=state['id']
IDS=list(IDS)
osm=[]
for i in range(len(IDS)):
    s=IDS[i]
    parts=s.rpartition('/')
    osm_id=parts[2]
    osm.append(osm_id)
state['OSM_id']=osm    

state_clean = state[["geometry", "OSM_id"]]


f=open('state.geojson', encoding="utf8")
data=json.load(f)
fet=data['features']
new_fet=[]#a new list with only polygon/multipolygon geometries

#remove all entries with point geometries

for i in range(len(fet)):
    
    fet_el=fet[i]
    geom_type=fet_el['geometry']['type']
    if geom_type=='Polygon' or geom_type=='MultiPolygon':
        new_fet.append(fet_el)
    else:
        pass

clean_fet=[]#remove the /relation before the osm_id#


for k in range(len(new_fet)):
    data_fet=new_fet[k]
    s_fet=data_fet['properties']['@id']
    parts=s_fet.rpartition('/')
    osm_id=parts[2]
    data_fet['properties']['@id']=osm_id
    new_key='ID'
    old_key='@id'
    prop=data_fet['properties']
    prop['ID']=prop.pop('@id')
    data_fet['properties']=prop
    clean_fet.append(data_fet)    

IDS=[]
names=[]

for k in range(len(clean_fet)):
    data_fet=clean_fet[k]
    osm_id=data_fet['properties']['ID']
    IDS.append((osm_id))
    
    name=data_fet['properties']['name']
    names.append(name)
    

main_data=pd.DataFrame({'OSM_id':IDS,'Names':names})    
df_merged=pd.merge(state_clean,main_data,on='OSM_id')
len(df_merged)






C:\Users\User\miniconda3\lib\site-packages\geopandas\geodataframe.py:1322: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super(GeoDataFrame, self).__setitem__(key, value)


1

In [9]:
#add (concatenate data on city-districts (Kriesfrie statds))
state_kries=gp.read_file('state_kries.geojson',encoding='utf8')
x=[]
for index, row in state_kries.iterrows():
    x.append(row['geometry'].geom_type)
state_kries['geomtype']=x    
state_kries = state_kries.drop(state_kries[state_kries.geomtype=='Point'].index)

rslt_df = state_kries[(state_kries['name']=='Kassel')|(state_kries['name']=='Darmstadt')|(state_kries['name']=='Frankfurt am Main')|(state_kries['name']=='Wiesbaden')|(state_kries['name']=='Offenbach am Main')]
#The geojson file for Hessen does not have information on the city-districts. Thats why we had to extract the subset of city
#districts manually.

IDS=rslt_df['id']
IDS=list(IDS)
osm=[]
for i in range(len(IDS)):
    s=IDS[i]
    parts=s.rpartition('/')
    osm_id=parts[2]
    osm.append(osm_id)
rslt_df['OSM_id']=osm 
state_kries_clean = rslt_df[["geometry", "OSM_id"]]

f=open('state_kries.geojson', encoding="utf8")
data=json.load(f)
fet=data['features']
new_fet=[]#a new list with only polygon/multipolygon geometries

#remove all entries with point geometries

for i in range(len(fet)):
    
    fet_el=fet[i]
    geom_type=fet_el['geometry']['type']
    if geom_type=='Polygon' or geom_type=='MultiPolygon':
        new_fet.append(fet_el)
    else:
        pass
    
clean_fet=[]#remove the /relation before the osm_id#

for k in range(len(new_fet)):
    data_fet=new_fet[k]
    s_fet=data_fet['properties']['@id']
    parts=s_fet.rpartition('/')
    osm_id=parts[2]
    data_fet['properties']['@id']=osm_id
    new_key='ID'
    old_key='@id'
    prop=data_fet['properties']
    prop['ID']=prop.pop('@id')
    data_fet['properties']=prop
    clean_fet.append(data_fet)
    len(clean_fet)   
    
    
IDS=[]
names=[]

for k in range(len(clean_fet)):
    data_fet=clean_fet[k]
    osm_id=data_fet['properties']['ID']
    IDS.append((osm_id))
    
    name=data_fet['properties']['name']
    names.append(name)
    

kries_data=pd.DataFrame({'OSM_id':IDS,'Names':names})


kries_merged=pd.merge(state_kries_clean,kries_data,on='OSM_id')
bigdata = pd.concat([df_merged, kries_merged], ignore_index=True, sort=False)








C:\Users\User\miniconda3\lib\site-packages\geopandas\geodataframe.py:1322: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super(GeoDataFrame, self).__setitem__(key, value)


In [10]:
#add data about post-offices that would be our proxies for populaton density
state_postboxes=gp.read_file('postboxes_state.geojson',encoding='utf8')
sjoined=gpd.sjoin(state_postboxes,bigdata,how='inner',op='within')#spatial join to allocate to a gemeinde.Check crs before sjoin
sjoined['lon'] = sjoined['geometry'].x
sjoined['lat'] = sjoined['geometry'].y

sjoined['combined'] = sjoined.apply(lambda x: list([x['lat'],
                                        x['lon']]),
                                        axis=1)   #create a column with the point coordinates a list


coods=sjoined.groupby('OSM_id')['combined'].apply(list).reset_index(name="Coords")#group by osm id
coods.head()
Total_boxes=[]
for i in range(len(coods)):
    r=coods.iloc[i]
    box_list=r['Coords']
    b=len(box_list)
    Total_boxes.append(b)

coods['Post_boxes']=Total_boxes    

coods.head()

m_box=np.array(Total_boxes)
np.min(m_box)


1

In [32]:
#set up requests module
import requests
from requests.adapters import HTTPAdapter
from requests.packages.urllib3.util.retry import Retry


def requests_retry_session(
    retries=5,
    backoff_factor=1,
    status_forcelist=(429,500, 502, 504),
    session=None,
):
    session = session or requests.Session()
    retry = Retry(
        total=retries,
        read=retries,
        connect=retries,
        backoff_factor=backoff_factor,
        status_forcelist=status_forcelist,
    )
    adapter = HTTPAdapter(max_retries=retry)
    session.mount('http://', adapter)
    session.mount('https://', adapter)
    return session


def query_bing(origins,mode):# send the coordinates to bing maps to get a matrix of travel times
    url_part1='https://dev.virtualearth.net/REST/v1/Routes/DistanceMatrix?origins'
    origins_string=';'.join(origins)
    url_part2=origins_string
    destinations_string=origins_string
    url_part3=destinations_string
    key_string='AtZvh0ap5znBNarSimgunq9TJGy-ekEgJTGGsm4PHZmxkihZ_D19E0F8VN6zj-pt'
    url_to_get=url_part1+'='+url_part2+'&destinations='+url_part3+'&travelMode='+mode+'&key='+key_string
    response=requests_retry_session().get(url_to_get)
    data=response.json()
    return(data)



def get_difference_direct(coords,max_origin):# get the difference by directly inputing the coordinates. Preferable over 
#get difference bing because it avoids having to call the overpass api and the bing api in a single call.
#The overpass API often returns a 429 error when called from within a for loop. This solution avoids loss of data
#because of malfunctioning of the the call to the overpass API. One less moving piece.
#since some gemeindes have a lost more post offices, it would makes sense to to condition the sampling 
    
    
    
    

    X = np.array(coords)
    
    n=[randint(0,len(X)-1)for p in range(0,max_origin)]
    Y=X[n]
    google_coord_strings=[]
    for i in range(len(Y)):
    
        c1=Y[i]
        c=str(c1[0])+','+str(c1[1])
        google_coord_strings.append(c)
    
    response_driving=query_bing(google_coord_strings,'driving')
    
    


    response_transit=query_bing(google_coord_strings,'transit')


    resource_driving=response_driving['resourceSets']
    resource_transit=response_transit['resourceSets']

    resource_set_driving=resource_driving[0]
    resource_set_transit=resource_transit[0]

    data_resouce_driving=resource_set_driving['resources']
    data_resouce_transit=resource_set_transit['resources']

    results_driving=data_resouce_driving[0]
    results_transit=data_resouce_transit[0]

    results_driving=results_driving['results']
    results_transit=results_transit['results']

    difference_duration=[]
    for i in range(len(results_driving)):
        
        d_D=results_driving[i]
        d_T=results_transit[i]
        time_driving=d_D['travelDuration']
        time_transit=d_T['travelDuration']
        difference=time_driving-time_transit
        difference_duration.append(difference)
        
    DIFF=np.array(difference_duration)
    penalty=(np.sum(DIFF))/(len(DIFF))
    penalty=penalty
    return(penalty)


# Breaking the data into chunks

Since the datasets has over 400 gemeinde, we need to break down our API calls into chunks and spread them over many days.
My key lets me make 50000 requests per day. However, its easy to hit the barrier. Crossing the daily limit leads to invalidation of the key. This would mean that one would have to request a new one. Additionally, the operation would not work.

## Save the data after finishing requests
Since the API requests are limited, it makes sense to be extremely prudent and save each data point after the receiving it. Thus the csv files should be updated continously. This would computationally very expensive with a large dataset. However, for the datasets that are considering in this application, the risk reduction is worth the small additional computational cost.

In [ ]:
#run 2



from tqdm import tqdm

coods_subset=coods[coods['Post_boxes']>=5]
batch_S=coods_subset.loc[coods_subset.Post_boxes<=10]

names=['OSM_id','Time Penalty']
billable_calls=0
blank_df2=pd.DataFrame(columns = names)
blank_df2.to_csv("mycsv2.csv",index=False)

for i in tqdm(range(len(batch_S))):
    df_0=pd.read_csv("mycsv2.csv")
    
    source_row=batch_S.iloc[i]
    osm_id=source_row['OSM_id']#fetch osm id from the coods dataframe
    coords=source_row['Coords']#fetch coodrinates from the coods dataframe
    b=source_row['Post_boxes']
    if b>100:#condition sampled points on the number of post offices
        max_origin=min(24,math.floor(b*0.1))
    elif b<100 and b>10:
        max_origin=10
    else:
        max_origin=b
        
    
    difference=get_difference_direct(coords,max_origin) #10 is the no of sampled post offices
    Result=[osm_id,difference]
    df_0.loc[len(df_0)] = Result
    df_0.to_csv("mycsv2.csv",index=False)
    
    sleep(3)
    


In [12]:
#run 3
from tqdm import tqdm

coods_subset=coods[coods['Post_boxes']>=5]
batch_M=coods_subset.loc[(coods_subset.Post_boxes>10) & (coods_subset.Post_boxes<=100)]

names=['OSM_id','Time Penalty']
billable_calls=0
blank_df2=pd.DataFrame(columns = names)
blank_df2.to_csv("mycsv3.csv",index=False)

for i in tqdm(range(len(batch_M))):
    df_0=pd.read_csv("mycsv3.csv")
    
    source_row=batch_M.iloc[i]
    osm_id=source_row['OSM_id']#fetch osm id from the coods dataframe
    coords=source_row['Coords']#fetch coodrinates from the coods dataframe
    b=source_row['Post_boxes']
    if b>100:#condition sampled points on the number of post offices
        max_origin=min(24,math.floor(b*0.1))
    elif b<100 and b>10:
        max_origin=10
    else:
        max_origin=b
        
    
    difference=get_difference_direct(coords,max_origin) #10 is the no of sampled post offices
    Result=[osm_id,difference]
    df_0.loc[len(df_0)] = Result
    df_0.to_csv("mycsv3.csv",index=False)
    
    sleep(3)
    


100%|████████████████████████████████████████████████████████████████████████████████| 150/150 [10:15<00:00,  4.10s/it]


OSM_id  Time Penalty
0  1112226     -4.098835
1  1115032     -9.475334
2  1115036     -4.986501
3   162356     -5.391660
4   163730     -5.371002

In [14]:
#run 4
from tqdm import tqdm

coods_subset=coods[coods['Post_boxes']>=5]
batch_L=coods_subset.loc[(coods_subset.Post_boxes>100)]

names=['OSM_id','Time Penalty']
billable_calls=0
blank_df2=pd.DataFrame(columns = names)
blank_df2.to_csv("mycsv4.csv",index=False)

for i in tqdm(range(len(batch_L))):
    df_0=pd.read_csv("mycsv4.csv")
    
    source_row=batch_L.iloc[i]
    osm_id=source_row['OSM_id']#fetch osm id from the coods dataframe
    coords=source_row['Coords']#fetch coodrinates from the coods dataframe
    b=source_row['Post_boxes']
    if b>100:#condition sampled points on the number of post offices
        max_origin=min(24,math.floor(b*0.1))
    elif b<100 and b>10:
        max_origin=10
    else:
        max_origin=b
        
    
    difference=get_difference_direct(coords,max_origin) #10 is the no of sampled post offices
    Result=[osm_id,difference]
    df_0.loc[len(df_0)] = Result
    df_0.to_csv("mycsv4.csv",index=False)
    
    sleep(3)
    


100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:18<00:00,  4.56s/it]


OSM_id  Time Penalty
0   62400    -10.480873
1   62496    -16.862168
2   62581     -9.521671
3   62598    -13.449805

In [60]:
final_1=pd.read_csv("mycsv2.csv")
final_2=pd.read_csv("mycsv3.csv")
final_3=pd.read_csv("mycsv4.csv")
my_Data=pd.concat([final_1, final_2,final_3], ignore_index=True, sort=False)
my_Data.to_csv("Final.csv",index=False)







In [58]:
my_Data['OSM_id']=my_Data['OSM_id'].astype(str)
geodf=pd.merge(bigdata,my_Data,on='OSM_id')
geodf['Time Penalty']=-1*geodf['Time Penalty']#since driving time is often lower than public transit time
geodf.head()

geometry  OSM_id        Names  \
0  POLYGON ((9.02611 50.23136, 9.02585 50.23166, ...   55158     Büdingen   
1  POLYGON ((9.02846 51.50875, 9.02807 51.50901, ...  162250  Diemelstadt   
2  POLYGON ((9.15491 51.44259, 9.15441 51.44251, ...  162251   Volkmarsen   
3  POLYGON ((9.03725 51.41458, 9.03753 51.41675, ...  162356  Bad Arolsen   
4  POLYGON ((8.70728 49.62986, 8.70719 49.62970, ...  163730   Mörlenbach   

   Time Penalty  
0     -5.955498  
1     30.981340  
2      5.048312  
3      5.391660  
4      5.371002

In [59]:
#Produce a map using folium. The geodf only has gemenides that have more than 5 post offices. Thus there are some holes in the 
#map

import branca


def rd2(x):
    return round(x, 2)


minimum, maximum = geodf["Time Penalty"].quantile([0.05, 0.95]).apply(rd2)


colormap = branca.colormap.LinearColormap(
    ['blue','red'],
    vmin=minimum,
    vmax=maximum,
)

colormap.caption = "Travel Time Penalty in Hessen"

colormap

import folium
from folium.plugins import Search


m = folium.Map(location=[49, 7.5], zoom_start=8)
def style_function(x):
    return {
        "fillColor": colormap(x["properties"]["Time Penalty"]),
        "color": "black",
        "weight": 2,
        "fillOpacity": 0.5,
    }


towngeo = folium.GeoJson(
    geodf,
    name="Gemeinde",
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(
        fields=["Names", "Time Penalty"], aliases=["Names", "Time Penalty"], localize=True
    ),
).add_to(m)



statesearch = Search(
    layer=towngeo,
    geom_type="Polygon",
    placeholder="Search for Gemeinde/Stadt",
    collapsed=False,
    search_label="Names",
    weight=3,
).add_to(m)


folium.LayerControl().add_to(m)
colormap.add_to(m)
m